In [1]:
# import datetime
import pandas as pd
import time
import os.path
import requests
from shutil import copyfile
import cProfile
import gdax

In [ ]:
period = 3
min_period = 0.3
currencies = ['BTC', 'ETH', 'LTC']
relays = ['EUR', 'USD']

pairs = []
for currency in currencies:
        for relay in relays:
            if currency != relay:
                pairs.append(currency+'-'+relay)

sinces = {}
for pair in pairs:
    trades_file = 'Data/trades_GDAX_' + pair + '.csv'
    print(pair)
    if os.path.isfile(trades_file):
        df_trades = pd.read_csv(trades_file, index_col=0, header=0)
    else:
        df_trades = pd.DataFrame(columns=['price','side','size','time','trade_id'])
        df_trades.to_csv(trades_file)
        df_trades.to_csv(trades_file+'bac')

    if len(df_trades) > 0:
        sinces[pair] = df_trades['trade_id'].iloc[-1]
    else:
        sinces[pair] = 0

print(sinces)
public_client = gdax.PublicClient()

BTC-EUR
BTC-USD
ETH-EUR
ETH-USD
LTC-EUR
LTC-USD
{'BTC-USD': 38434708, 'ETH-EUR': 3368817, 'LTC-USD': 0, 'BTC-EUR': 12656869, 'ETH-USD': 29941415, 'LTC-EUR': 0}


In [ ]:
def update_trades(pair, since):
    trades_file = 'Data/trades_GDAX_' + pair + '.csv'
    
    try:
        time.sleep(period)
        trades = public_client.get_product_trades(product_id=pair)
    except (KeyboardInterrupt, SystemExit):
        raise
    except:
        print(pair, "except")
        pass
    else:
        if len(trades) > 0:
#             print(trades)
            df_temp = pd.DataFrame(data=trades, columns=['price','side','size','time','trade_id'])
            df_temp[['size','price']] = df_temp[['size','price']].astype('float64')
            df_temp.index = df_temp['trade_id'].values
            
            df_temp = df_temp.sort_index()
            df_temp = df_temp[df_temp.index > since]
#             print(df_temp)

            try:
                copyfile(trades_file, trades_file+'temp')
                df_temp.to_csv(trades_file+'temp', mode='a', header=0)
                os.replace(trades_file+'temp', trades_file)
                copyfile(trades_file, trades_file+'bac')
                since = df_temp['trade_id'].iloc[-1]
            except:
                print(pair, "Problem zapisu")
                copyfile(trades_file+'bac', trades_file)          

            print(pair, df_temp.tail(1))
            
    return since


def run():
    for i in range(1):
        for pair in pairs:
            sinces[pair] = update_trades(pair=pair, since=sinces[pair])
  

while True:
    for pair in pairs:
        sinces[pair] = update_trades(pair=pair, since=sinces[pair])

        
# cProfile.run('run()')

BTC-EUR             price side      size                      time  trade_id
12660378  9039.86  buy  0.131984  2018-03-02T08:41:13.123Z  12660378
BTC-USD              price  side    size                      time  trade_id
38446225  11098.67  sell  0.0719  2018-03-02T08:41:37.511Z  38446225
ETH-EUR           price side    size                      time  trade_id
3369820  711.58  buy  0.5136  2018-03-02T08:41:30.839Z   3369820
ETH-USD            price  side    size                      time  trade_id
29947933  870.58  sell  0.8382  2018-03-02T08:41:40.574Z  29947933
LTC-EUR          price side       size                      time  trade_id
2760555  170.5  buy  40.955326  2018-03-02T08:41:47.259Z   2760555
LTC-USD            price  side      size                      time  trade_id
26885311  208.55  sell  10.73471  2018-03-02T08:41:41.932Z  26885311
BTC-EUR            price  side      size                      time  trade_id
12660394  9040.0  sell  0.101337  2018-03-02T08:41:56.364Z  126

BTC-USD              price side    size                      time  trade_id
38446249  11098.66  buy  0.0707  2018-03-02T08:44:57.055Z  38446249
ETH-EUR           price side      size                      time  trade_id
3369829  711.58  buy  0.034722  2018-03-02T08:45:02.582Z   3369829
ETH-USD            price  side    size                      time  trade_id
29947994  870.75  sell  0.4975  2018-03-02T08:45:10.417Z  29947994
LTC-EUR           price side      size                      time  trade_id
2760591  170.17  buy  1.338072  2018-03-02T08:45:16.486Z   2760591
LTC-USD            price side    size                      time  trade_id
26885348  208.53  buy  1.9089  2018-03-02T08:45:18.857Z  26885348
BTC-EUR            price  side      size                      time  trade_id
12660426  9040.0  sell  0.016552  2018-03-02T08:45:29.478Z  12660426
BTC-USD              price side   size                      time  trade_id
38446250  11098.66  buy  0.024  2018-03-02T08:45:21.982Z  38446250
ET

ETH-EUR           price  side    size                      time  trade_id
3369834  711.59  sell  1.4011  2018-03-02T08:48:47.905Z   3369834
ETH-USD           price  side     size                      time  trade_id
29948119  868.7  sell  1.39042  2018-03-02T08:48:53.098Z  29948119
LTC-EUR Problem zapisu
LTC-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
LTC-USD            price  side    size                      time  trade_id
26885414  208.12  sell  0.4596  2018-03-02T08:48:44.052Z  26885414
BTC-EUR            price  side  size                      time  trade_id
12660482  9040.0  sell  0.05  2018-03-02T08:49:08.116Z  12660482
BTC-USD              price side      size                      time  trade_id
38446354  11081.29  buy  0.089664  2018-03-02T08:49:09.926Z  38446354
ETH-EUR Problem zapisu
ETH-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
ETH-USD            price  side      size                      time  trade_id
29948130 

LTC-EUR           price side      size                      time  trade_id
2760605  170.16  buy  5.656627  2018-03-02T08:52:28.519Z   2760605
LTC-USD            price  side   size                      time  trade_id
26885471  208.13  sell  0.421  2018-03-02T08:52:40.916Z  26885471
BTC-EUR             price  side  size                      time  trade_id
12660563  9030.42  sell  0.03  2018-03-02T08:52:43.634Z  12660563
BTC-USD             price  side    size                      time  trade_id
38446403  11081.3  sell  0.6858  2018-03-02T08:52:48.774Z  38446403
ETH-EUR Problem zapisu
ETH-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
ETH-USD            price side    size                     time  trade_id
29948212  869.98  buy  0.5608  2018-03-02T08:52:39.25Z  29948212
LTC-EUR           price  side      size                      time  trade_id
2760606  170.17  sell  1.469119  2018-03-02T08:52:47.983Z   2760606
LTC-USD Problem zapisu
LTC-USD Empty DataFrame
Col

BTC-EUR             price  side  size                     time  trade_id
12660643  9036.99  sell  0.01  2018-03-02T08:56:26.02Z  12660643
BTC-USD              price  side      size                      time  trade_id
38446460  11074.89  sell  0.001202  2018-03-02T08:56:28.348Z  38446460
ETH-EUR Problem zapisu
ETH-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
ETH-USD            price  side      size                      time  trade_id
29948334  868.81  sell  0.038889  2018-03-02T08:56:37.438Z  29948334
LTC-EUR Problem zapisu
LTC-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
LTC-USD            price  side    size                      time  trade_id
26885502  208.04  sell  0.1423  2018-03-02T08:56:36.025Z  26885502
BTC-EUR             price side  size                      time  trade_id
12660662  9035.01  buy  0.01  2018-03-02T08:56:46.747Z  12660662
BTC-USD             price  side      size                      time  trade_id
3844

...

LTC-USD            price  side    size                      time  trade_id
26933242  213.83  sell  0.9322  2018-03-03T12:10:48.624Z  26933242
BTC-EUR             price  side  size                      time  trade_id
12689816  9146.98  sell  0.01  2018-03-03T12:10:55.284Z  12689816
BTC-USD              price  side    size                      time  trade_id
38511976  11291.37  sell  0.0069  2018-03-03T12:11:01.237Z  38511976
ETH-EUR Problem zapisu
ETH-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
ETH-USD           price  side   size                      time  trade_id
29990025  864.0  sell  0.207  2018-03-03T12:10:59.569Z  29990025
LTC-EUR           price  side  size                      time  trade_id
2767815  172.52  sell   5.0  2018-03-03T12:11:06.566Z   2767815
LTC-USD            price  side    size                      time  trade_id
26933249  213.86  sell  0.5839  2018-03-03T12:11:10.716Z  26933249
BTC-EUR             price side      size              

ETH-USD            price  side      size                      time  trade_id
29990258  864.49  sell  2.008052  2018-03-03T12:19:25.105Z  29990258
LTC-EUR          price  side      size                      time  trade_id
2767881  173.2  sell  0.089291  2018-03-03T12:19:30.761Z   2767881
LTC-USD            price  side    size                      time  trade_id
26933380  214.25  sell  3.4327  2018-03-03T12:19:36.007Z  26933380
BTC-EUR             price side  size                      time  trade_id
12689963  9146.99  buy  0.02  2018-03-03T12:19:27.031Z  12689963
BTC-USD              price  side      size                      time  trade_id
38512056  11301.71  sell  0.000126  2018-03-03T12:19:40.769Z  38512056
ETH-EUR           price  side      size                      time  trade_id
3378250  700.51  sell  0.475804  2018-03-03T12:19:43.827Z   3378250
ETH-USD            price  side    size                      time  trade_id
29990279  864.06  sell  0.2854  2018-03-03T12:19:49.687Z  29990

ETH-USD            price  side    size                      time  trade_id
29990369  864.31  sell  0.1536  2018-03-03T12:22:58.829Z  29990369
LTC-EUR Problem zapisu
LTC-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
LTC-USD            price side    size                      time  trade_id
26933401  214.24  buy  4.6474  2018-03-03T12:23:09.007Z  26933401
BTC-EUR             price  side      size                     time  trade_id
12690020  9149.99  sell  1.969179  2018-03-03T12:23:12.54Z  12690020
BTC-USD             price  side    size                      time  trade_id
38512164  11325.0  sell  0.0112  2018-03-03T12:23:03.528Z  38512164
ETH-EUR           price  side      size                      time  trade_id
3378267  700.56  sell  0.021347  2018-03-03T12:23:10.243Z   3378267
ETH-USD            price  side   size                      time  trade_id
29990370  864.31  sell  0.014  2018-03-03T12:23:11.339Z  29990370
LTC-EUR Problem zapisu
LTC-EUR Empty DataF

BTC-EUR Problem zapisu
BTC-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
BTC-USD             price  side    size                      time  trade_id
38512215  11325.0  sell  0.0138  2018-03-03T12:29:13.708Z  38512215
ETH-EUR Problem zapisu
ETH-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
ETH-USD           price  side    size                      time  trade_id
29990446  864.5  sell  1.2225  2018-03-03T12:29:16.611Z  29990446
LTC-EUR Problem zapisu
LTC-EUR Empty DataFrame
Columns: [price, side, size, time, trade_id]
Index: []
LTC-USD            price side    size                      time  trade_id
26933528  214.45  buy  1.3356  2018-03-03T12:29:25.746Z  26933528
BTC-EUR            price  side  size                      time  trade_id
12690092  9151.0  sell  0.01  2018-03-03T12:29:32.537Z  12690092
BTC-USD              price side     size                      time  trade_id
38512646  11368.99  buy  0.01103  2018-03-03T12:31:07.8

BTC-USD             price  side    size                      time  trade_id
38513008  11391.0  sell  0.1163  2018-03-03T12:35:23.447Z  38513008
ETH-EUR           price  side       size                      time  trade_id
3378383  704.35  sell  35.580352  2018-03-03T12:35:25.849Z   3378383
ETH-USD            price  side      size                      time  trade_id
29990573  865.46  sell  1.039494  2018-03-03T12:35:30.284Z  29990573
LTC-EUR           price  side       size                      time  trade_id
2768008  173.99  sell  14.325665  2018-03-03T12:35:27.249Z   2768008
LTC-USD            price  side     size                      time  trade_id
26933863  215.25  sell  0.34739  2018-03-03T12:35:36.456Z  26933863
BTC-EUR             price side     size                     time  trade_id
12690471  9195.99  buy  0.03633  2018-03-03T12:35:39.63Z  12690471
BTC-USD             price  side    size                      time  trade_id
38513015  11391.0  sell  0.1219  2018-03-03T12:35:35.553